In [1]:
# noexport
!typech difficulty_choices.ipynb

[NbConvertApp] Converting notebook difficulty_choices.ipynb to python
Success: no issues found in 1 source file


In [1]:
from train_utils import *


In [2]:
#import plot_utils
#reload(plot_utils)
from plot_utils import *


In [3]:
def get_difficulty_choices_heatmap():
  users_with_difficulty = get_users_with_choose_difficulty()
  user_to_difficulty_items = {}
  for user in users_with_difficulty:
    difficulty_items = get_choose_difficulty_items_for_user(user)
    difficulty_items = [x for x in difficulty_items if x.get('is_random') == False]
    if len(difficulty_items) < 200:
      continue
    user_to_difficulty_items[user] = difficulty_items
  user_to_heatmap_row = {}
  user_to_mean_difficulty = {}
  for user,difficulty_items in user_to_difficulty_items.items():
    heatmap_row = []
    for item in difficulty_items[:200]:
      difficulty = item['difficulty']
      difficulty_idx = ['nothing', 'easy', 'medium', 'hard'].index(difficulty)
      heatmap_row.append(difficulty_idx)
    user_to_heatmap_row[user] = heatmap_row
    user_to_mean_difficulty[user] = np.mean(heatmap_row)
  user_list = list(user_to_heatmap_row.keys())
  user_list.sort(key = lambda x: user_to_mean_difficulty[x])
  heatmap_data = []
  for user in user_list:
    heatmap_data.append(user_to_heatmap_row[user])
  return heatmap_data

In [4]:
def get_israndom_choices_heatmap_everytime():
  users_with_difficulty = get_users_with_choose_difficulty()
  user_to_israndom_items = {}
  for user in users_with_difficulty:
    abtest_settings = get_abtest_settings(user)
    if abtest_settings.get('frequency_of_choose_difficulty') != '1.0':
      continue
    difficulty_items = get_choose_difficulty_items_for_user(user)
    difficulty_items = [x for x in difficulty_items if 'is_random' in x]
    israndom_items = [int(x['is_random'] == False) for x in difficulty_items]
    if len(israndom_items) < 400:
      continue
    user_to_israndom_items[user] = israndom_items
  user_to_heatmap_row = {}
  user_to_mean = {}
  for user,israndom_items in user_to_israndom_items.items():
    heatmap_row = israndom_items[:400]
    user_to_heatmap_row[user] = heatmap_row
    user_to_mean[user] = np.mean(heatmap_row)
  user_list = list(user_to_heatmap_row.keys())
  user_list.sort(key = lambda x: user_to_mean[x])
  heatmap_data = []
  for user in user_list:
    heatmap_data.append(user_to_heatmap_row[user])
  return heatmap_data


In [5]:
def get_israndom_choices_heatmap():
  users_with_difficulty = get_users_with_choose_difficulty()
  user_to_israndom_items = {}
  for user in users_with_difficulty:
    abtest_settings = get_abtest_settings(user)
    if abtest_settings.get('frequency_of_choose_difficulty') != '0.5':
      continue
    difficulty_items = get_choose_difficulty_items_for_user(user)
    difficulty_items = [x for x in difficulty_items if 'is_random' in x]
    israndom_items = [int(x['is_random'] == False) for x in difficulty_items]
    if len(israndom_items) < 400:
      continue
    user_to_israndom_items[user] = israndom_items
  user_to_heatmap_row = {}
  user_to_mean = {}
  for user,israndom_items in user_to_israndom_items.items():
    heatmap_row = israndom_items[:400]
    user_to_heatmap_row[user] = heatmap_row
    user_to_mean[user] = np.mean(heatmap_row)
  user_list = list(user_to_heatmap_row.keys())
  user_list.sort(key = lambda x: user_to_mean[x])
  heatmap_data = []
  for user in user_list:
    heatmap_data.append(user_to_heatmap_row[user])
  return heatmap_data


In [6]:
import plot_utils
from imp import reload
reload(plot_utils)
from plot_utils import *

def plot_israndom_choices_heatmap():
  heatmap_data = get_israndom_choices_heatmap()
  plot_heatmap(
    heatmap_data,
    title = 'Changes in user willingness to choose intervention difficulty over time',
    xlabel = 'i-th time the user is seeing the difficulty selection prompt',
    ylabel = 'User index',
    colorscale = [
      [0.0, 'rgb(255, 255, 255)'],
      [0.5, 'rgb(255, 255, 255)'],
      [0.5, 'rgb(0, 0, 0)'],
      [1.0, 'rgb(0, 0, 0)'],
    ],
    ticktext = ['User chose', 'No choice (random)'],
  )


In [7]:
# noexport

plot_israndom_choices_heatmap()

In [8]:
def plot_difficulty_choices_heatmap():
  heatmap_data = get_difficulty_choices_heatmap()
  plot_heatmap(
    heatmap_data,
    title = 'Changes in user difficulty choices over time',
    xlabel = 'i-th time the user is choosing difficulty',
    ylabel = 'User index',
    #colorscale = 'Greys',
    # 67, 7, 83. 52, 105, 139. 61, 182, 122. 252, 229, 64
    colorscale = [
      [0.0, 'rgb(67, 7, 83)'],
      [0.25, 'rgb(67, 7, 83)'],
      [0.25, 'rgb(52, 105, 139)'],
      [0.50, 'rgb(52, 105, 139)'],
      [0.50, 'rgb(61, 182, 122)'],
      [0.75, 'rgb(61, 182, 122)'],
      [0.75, 'rgb(252, 229, 64)'],
      [1.0, 'rgb(252, 229, 64)'],
    ],
    ticktext = ['No Intervention', 'Easy', 'Medium', 'Hard'],
  )



In [9]:
# noexport

#len(get_difficulty_choices_heatmap())
plot_difficulty_choices_heatmap()

In [10]:
# noexport

difficulty_choices_heatmap = get_difficulty_choices_heatmap()

num_choices = len(difficulty_choices_heatmap[0])
num_users = len(difficulty_choices_heatmap)
difficulty_choice_to_choice_num_idx_to_counts = [[0]*num_choices for x in range(4)]
for choice_num_idx in range(num_choices):
  for user_idx in range(num_users):
    difficulty_choice = difficulty_choices_heatmap[user_idx][choice_num_idx]
    difficulty_choice_to_choice_num_idx_to_counts[difficulty_choice][choice_num_idx] += 1
    #difficulty_choice_idx_to_counts[]

difficulty_choice_to_choice_num_idx_to_percent = [[0]*num_choices for x in range(4)]
total = sum([x[0] for x in difficulty_choice_to_choice_num_idx_to_counts])
for difficulty_choice in range(4):
  for choice_num_idx in range(num_choices):
    difficulty_choice_to_choice_num_idx_to_percent[difficulty_choice][choice_num_idx] = difficulty_choice_to_choice_num_idx_to_counts[difficulty_choice][choice_num_idx] / total

difficulty_choice_names = ['No Intervention', 'Easy', 'Medium', 'Hard']
plot_data([
  go.Scatter(
    x=list(range(len(choice_num_idx_to_counts))),
    y=choice_num_idx_to_counts,
    name=difficulty_choice_names[idx],
  )
  for idx,choice_num_idx_to_counts in enumerate(difficulty_choice_to_choice_num_idx_to_percent)
],
title='Changes in user difficulty choices over time',
ylabel='Fraction of users',
xlabel='i-th time the user is choosing difficulty',
font={'size': 16},
)